In [ ]:
import os
import numpy
import datetime

### Retrieve data from SEAScope
SEAScope must be running and you must click on the "Extract granule data button" in the contextual menu.

In [ ]:
# Load extracted data directly from the viewer memory
from SEAScope.lib import get_extracted_data
extractions = get_extracted_data()
print('\n=> Available granules \n')
print('\n'.join(['\t• {}\n'.format(uri) for uri in extractions]))

In [ ]:
granule_uri = ''  # /!\ Change this

extraction = extractions[granule_uri]
print('\n=> Available fields \n')
print('\n'.join(['\t• {}'.format(field) for field in extraction['data']]))

In [ ]:
field_name = ''  # /!\ Change this

data = extraction['data'][field_name]

### Display extracted data

In [ ]:
import matplotlib
%matplotlib inline
matplotlib.pyplot.pcolormesh(data, cmap='jet',
                             vmin=numpy.min(data),
                             vmax=numpy.max(data))

### Modify data


In [ ]:
mask = (data.mask | numpy.isnan(data))
new_data = data[:, :]
new_data._sharedmask = False
new_data[numpy.where(mask)] = 1
new_data = numpy.log(numpy.abs(.1 + new_data)) # Just an example...
new_data[numpy.where(mask)] = numpy.ma.masked

In [ ]:
matplotlib.pyplot.pcolormesh(new_data, cmap='jet')

In [ ]:
new_data2 = -3.2 + new_data * 50

In [ ]:
matplotlib.pyplot.pcolormesh(new_data2, cmap='jet')

### Sending data to SEAScope

A granule has to belong to a collection, this is mandatory for SEAScope, so let's create a collection.

In [12]:
from SEAScope.lib.utils import create_collection, init_ids
init_ids(10, 1000)
# Make sur to keep the collection identifier, we will need it later
collection_id, collection = create_collection('User - New data')
print(collection_id)

16


Now that we have a collection, we can create the "shell" of the granule, ie. define where and when the granule will appear

In [ ]:
from SEAScope.lib.utils import create_granule

f = 1

# We want this granule to appear where the extraction took place,
# so we reuse the GCPs of the extraction
gcps = extraction['meta']['gcps']

start = datetime.datetime(2015, 12, max(1, f * 10))
stop = datetime.datetime(2015, 12, (f+1) * 10)

granule_id, granule = create_granule(collection_id, gcps, start, stop)

The granule will contain each matrix of modified data as what we call a "field"

In [ ]:
from SEAScope.lib.utils import set_field

set_field(granule, 'vec_U', (f + 0.1) * new_data)
set_field(granule, 'vec_V', (f + 0.1) * new_data2)

Now let's upload the collection and granule to SEAScope

In [13]:
import SEAScope.upload

# IP address and port used to reach the SEAScope standalone application
host = '127.0.0.1'
port = 11155

with SEAScope.upload.connect(host, port) as link:
    # Send create collection job
    SEAScope.upload.collection(link, collection)
    
    # Send create granule job
    SEAScope.upload.granule(link, granule)

Closing connection


In [ ]:
print(collection_id, granule_id)

### Telling SEAScope what to display

The next step is variables definition. A variable may be composed of
one or two fields (in which case they are considered to be horizontal and
vertical components of a vector).

In [ ]:
from SEAScope.lib.utils import create_variable

# Create a variable for the horizontal component
h_variable = create_variable(collection, 'Horizontal', ['vec_U'])

# Create a variable for the vertical component
v_variable = create_variable(collection, 'Vertical', ['vec_V'])

# Create a variable for the complete vector
vector_variable = create_variable(collection, 'Vector', ['vec_U', 'vec_V'])

if None in (h_variable, v_variable, vector_variable):
    print()
    raise Exception('Re-creating existing variables is not possible.')

In [ ]:
with SEAScope.upload.connect(host, port) as link:
    # Send create variable jobs
    SEAScope.upload.variable(link, h_variable)
    SEAScope.upload.variable(link, v_variable)
    SEAScope.upload.variable(link, vector_variable)

### Telling SEAScope how to display variables

In [ ]:
from SEAScope.lib.utils import create_rendering_config

# Rendering configuration for the horizontal component
h_rcfg = h_variable['rendering']
h_rcfg['min'] = numpy.min(new_data)
h_rcfg['max'] = numpy.max(new_data)
h_rcfg['colormap'] = 'jet'

# Rendering configuration for the vertical component
v_rcfg = v_variable['rendering']
v_rcfg['min'] = numpy.min(new_data2)
v_rcfg['max'] = numpy.max(new_data2)
v_rcfg['colormap'] = 'rainbow'
v_rcfg['opacity'] = 0.3
v_rcfg['filterMode'] = 'BILINEAR'

# Rendering configuration for the complete vector
vector_rcfg = vector_variable['rendering']
vector_rcfg['min'] = 0.0
vector_rcfg['max'] = 100.0

In [ ]:
with SEAScope.upload.connect(host, port) as link:
    # Send create rendering config jobs
    SEAScope.upload.rendering_config(link, h_rcfg)
    SEAScope.upload.rendering_config(link, v_rcfg)
    SEAScope.upload.rendering_config(link, vector_rcfg)

In [ ]:
print(granule_id, collection_id)

Done!